## Import packages 

In [84]:
# GET PARAMETERS
import os
import sys
import pandas as pd 
import geopandas as gpd
import pickle 
import torch
# Get Parent folder : 
current_path = os.getcwd()
parent_dir = os.path.abspath(os.path.join(current_path, '..'))
if parent_dir not in sys.path:
    sys.path.insert(0, parent_dir)

from build_inputs.load_contextual_data import replace_heure_d_ete
from load_inputs.Lyon.netmob.netmob_POIs import load_data_npy,START,END,FREQ
from argparse import Namespace

# Load Subway Volume : 

In [85]:
coverage_local = pd.date_range(start=START, end=END, freq=FREQ)[:-1]
FOLDER_PATH = os.path.expanduser('~/../../../data/rrochas/prediction_validation')
df_stations = pd.read_csv(f'{FOLDER_PATH}/subway_in/subway_in.csv',index_col=0)
df_stations.index = pd.to_datetime(df_stations.index)
df_stations = df_stations.reindex(coverage_local)

df_stations.head()

Ampère Victor Hugo  Bellecour  Brotteaux  Charpennes  \
2019-03-16 00:00:00                34.0      396.0       37.0       164.0   
2019-03-16 00:15:00                40.0      298.0       56.0       164.0   
2019-03-16 00:30:00                17.0      258.0       24.0        74.0   
2019-03-16 00:45:00                 1.0       44.0        3.0        13.0   
2019-03-16 01:00:00                 0.0        0.0        0.0         3.0   

                     Cordeliers  Croix Paquet  Croix-Rousse  Cuire  Cusset  \
2019-03-16 00:00:00       143.0           6.0          33.0   17.0    24.0   
2019-03-16 00:15:00       139.0           3.0          46.0    7.0    20.0   
2019-03-16 00:30:00       100.0          19.0           6.0    0.0     4.0   
2019-03-16 00:45:00        13.0           1.0           6.0    3.0     2.0   
2019-03-16 01:00:00         0.0           0.0           0.0    0.0     5.0   

                     Debourg  ...  Part-Dieu  Perrache  Place Guichard  \
2019-03-16 00:00:00     40.0  ...       68.0     144.0            26.0   
2019-03-16 00:15:00     46.0  ...       77.0     145.0            31.0   
2019-03-16 00:30:00     13.0  ...       43.0      55.0            15.0   
2019-03-16 00:45:00      2.0  ...        6.0       5.0             3.0   
2019-03-16 01:00:00      0.0  ...        0.0       0.0             4.0   

                     Place Jean Jaurès  République Villeurbanne  Sans Souci  \
2019-03-16 00:00:00               48.0                     53.0        55.0   
2019-03-16 00:15:00               32.0                     45.0        55.0   
2019-03-16 00:30:00               19.0                      4.0        45.0   
2019-03-16 00:45:00                4.0                      0.0        13.0   
2019-03-16 01:00:00                4.0                      2.0         2.0   

                     Saxe - Gambetta  Stade de Gerland  Valmy  Vieux Lyon  
2019-03-16 00:00:00            112.0              59.0   71.0       155.0  
2019-03-16 00:15:00            159.0              56.0   41.0       149.0  
2019-03-16 00:30:00             98.0               4.0   72.0       127.0  
2019-03-16 00:45:00             17.0               4.0    3.0        12.0  
2019-03-16 01:00:00              0.0               0.0    1.0         0.0  

[5 rows x 40 columns]

## Load NetMob Data: 

In [92]:
iris_target_n = None# 30 # None # 100
apps = ['Web_Weather'] # Deezer # Google_Maps # Web_Weather
args = Namespace(**{'contextual_kwargs':{'netmob_POIs':{'NetMob_selected_apps': apps,
                                                        'NetMob_transfer_mode' : ['DL'],
                                                        'NetMob_selected_tags':['iris'],
                                                        'NetMob_expanded':'',
                                                        'agg_iris_target_n': iris_target_n,
                                                       },
                                        }
                    })
netmob_T = load_data_npy(FOLDER_PATH,args)
netmob_T = netmob_T.permute(1,0)
netmob_T = replace_heure_d_ete(netmob_T,start = 1532, end = 1536)  # start = 1532, end = 1536  # start = 572, end = 576
coverage_local = pd.date_range(start=START, end=END, freq=FREQ)[:-1]

if iris_target_n is None:
    gdf = gpd.read_file(f'{FOLDER_PATH}/lyon_iris_shapefile/lyon.shp')
    dictionnary_aggregated_iris = None
else: 
    gdf = gpd.read_file(f'{FOLDER_PATH}/lyon_iris_agg{iris_target_n}/lyon.shp')
    dic_path = f"/home/rrochas/../../../data/rrochas/prediction_validation/dic_lyon_iris_agg{iris_target_n}.pkl"
    dictionnary_aggregated_iris = pickle.load(open(dic_path,'rb'))



df_dates = pd.DataFrame(dict(dates = coverage_local,
    weekday = coverage_local.weekday,
                  hour = coverage_local.hour,
                  minute = coverage_local.minute))

# Deezer App Consumption on Monday 2019-03-19 at 7:30am

In [87]:
import numpy as np 
vmax = 0

s_flow_at_7_30 = pd.read_csv(f'{FOLDER_PATH}/../../NetMob/NetMob_raw/{apps[0]}/20190319/Lyon_{apps[0]}_20190319_DL.txt',sep = ' ',header=None)[7*4]
local_vmax = s_flow_at_7_30.quantile(0.975)
s_flow_at_7_30[s_flow_at_7_30 > local_vmax] = local_vmax
if local_vmax > vmax:
    vmax = local_vmax

s_flow_at_8 = pd.read_csv(f'{FOLDER_PATH}/../../NetMob/NetMob_raw/{apps[0]}/20190319/Lyon_{apps[0]}_20190319_DL.txt',sep = ' ',header=None)[7*4+2]
local_vmax = s_flow_at_8.quantile(0.975)
s_flow_at_8[s_flow_at_8 > local_vmax] = local_vmax
if local_vmax > vmax:
    vmax = local_vmax

s_flow_at_8_30 = pd.read_csv(f'{FOLDER_PATH}/../../NetMob/NetMob_raw/{apps[0]}/20190319/Lyon_{apps[0]}_20190319_DL.txt',sep = ' ',header=None)[7*4+4]
local_vmax = s_flow_at_8_30.quantile(0.975)
s_flow_at_8_30[s_flow_at_8_30 > local_vmax] = local_vmax
if local_vmax > vmax:
    vmax = local_vmax

s_flow_at_9 = pd.read_csv(f'{FOLDER_PATH}/../../NetMob/NetMob_raw/{apps[0]}/20190319/Lyon_{apps[0]}_20190319_DL.txt',sep = ' ',header=None)[7*4+6]
local_vmax = s_flow_at_9.quantile(0.975)
s_flow_at_9[s_flow_at_9 > local_vmax] = local_vmax
if local_vmax > vmax:
    vmax = local_vmax

gdf_tile = gpd.read_file(f'{FOLDER_PATH}/NetMob_lyon.geojson')
gdf_tile[f'{apps[0]} traffic consumption at 7:30am'] = s_flow_at_7_30
gdf_tile[f'{apps[0]} traffic consumption at 8:00am'] = s_flow_at_8
gdf_tile[f'{apps[0]} traffic consumption at 8:30am'] = s_flow_at_8_30
gdf_tile[f'{apps[0]} traffic consumption at 9:00am'] = s_flow_at_9

# Load usefull geometry shell: 
geom_all =  gpd.GeoDataFrame(dict(geometry=[gdf['geometry'].unary_union]))
geom_all.crs = 'EPSG:2154'
geom_all = geom_all.to_crs(gdf_tile.crs)

# Extract sub-gdf: 
gdf_tile = gdf_tile.sjoin(geom_all)

## Visualisation : 

In [ ]:
# gdf_tile.explore(f'{apps[0]} traffic consumption at 7:30am',vmax = vmax,tiles = 'cartodb positron')
# gdf_tile.explore(f'{apps[0]} traffic consumption at 8:00am',vmax = vmax,tiles = 'cartodb positron')
# gdf_tile.explore(f'{apps[0]} traffic consumption at 8:30am',vmax = vmax,tiles = 'cartodb positron')
# gdf_tile.explore(f'{apps[0]} traffic consumption at 9:00am',vmax = vmax,tiles = 'cartodb positron')

## Focus on aggregated data: 

In [ ]:
# masked monday 7:30:
monday_date = coverage_local[30+96*3]
mask = df_dates['dates'].isin([monday_date])
index_mask = df_dates.index[mask]
masked_monday_7_30_NetMob =  torch.index_select(netmob_T,0,torch.tensor(index_mask).long())
monday_7_30 = masked_monday_7_30_NetMob.sum(0)

def proportion_volume(row,dictionnary_aggregated_iris,column):
    nb_iris = len(dictionnary_aggregated_iris[row.CODE_IRIS])
    row[column] = row[column] * nb_iris
    return row

gdf['Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)'] = (monday_7_30.numpy())
if dictionnary_aggregated_iris is not None: 
    gdf = gdf.apply(lambda row : proportion_volume(row,dictionnary_aggregated_iris,'Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)'),axis = 1)

gdf['Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)'] = (gdf['Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)']/1e3).round().astype(int)
gdf[['CODE_IRIS','geometry','Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)']].explore('Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)', tiles = 'CartoDB positron',
            vmin = 0, vmax = min(gdf['Deezer Consumption on Monday 2019-03-19 7:30am (Arbitrary Units)'].quantile(0.95),50000)
           )

# Plot Time-Serie Profile

In [267]:
from plotting.TS_analysis import plot_subway_patterns
from bokeh.palettes import Turbo256 as palette
from bokeh.plotting import show,output_notebook

# 1. Select the subway station : 
stations_i = 'Charpennes'

# 2. Select the Zones of interest :
if iris_target_n == 100 :
    charp_iris = 692660901 # Grouped Iris Charpennes - Republique - Gratte-ciel
    massena_iris = 693860302 # Grouped Massena Foch
    park_iris = 693860103 # Grouped Tête d'Or
    part_dieu_iris = 693830402 # Grouped Iris Part Dieu 
    zones_ids = [charp_iris,massena_iris,park_iris,part_dieu_iris]
    columns =  ['Charpennes','Massena','Tête d\'Or','Part Dieu']

if iris_target_n == 50:
    villeurbanne_NE = 692660901 # Villeurbane North-East
    Massena_caluire = 690340502
    Lyon3_W = 693880202 # Lyon 3 OUest
    Lyon3_E =  693820302 # Lyon 3 Est
    zones_ids = [villeurbanne_NE,Massena_caluire,Lyon3_W,Lyon3_E]
    columns =  ['Villeurbanne NE','Massena Caluire','Lyon 3 Ouest','Lyon 3 Est']

if iris_target_n == 30:
    Villeurbanne_N_and_caluire = 690340602
    zones_ids = [Villeurbanne_N_and_caluire]
    columns =  ['Villeurbanne_N_and_caluire']

# 3. Extract zones index 

zones_index = gdf[gdf.CODE_IRIS.isin(zones_ids)].index

# 4. Extract the NetMob consumption for the zones of interest and add subway station passenger flow : 
df_NetMob_consumption = pd.DataFrame(torch.index_select(netmob_T,1,torch.tensor(zones_index).long()),columns = columns,index = coverage_local)
df_NetMob_consumption['Subway-Station'] = df_stations[stations_i]

# 5. MinMax Normalization of columns: 
df_NetMob_consumption = (df_NetMob_consumption - df_NetMob_consumption.min()) / (df_NetMob_consumption.quantile(0.99) - df_NetMob_consumption.min())

# 6. Plotting : 

p1 = plot_subway_patterns(df_NetMob_consumption,columns+['Subway-Station'],palette,width=1500,height=400,title=f'Trafic Volume of {apps[0]} by stations')
output_notebook()
show(p1)

Loading BokehJS ...

In [212]:
df_NetMob_consumption


Charpennes     Massena     Tête d'Or      Part Dieu  Subway-Station
0     1.439495e+06  1758757.00  5.861699e+05  657037.187500             NaN
1     1.262794e+06   477268.25  6.680860e+05  627238.312500             NaN
2     6.414963e+05   331929.50  4.400854e+05  261233.109375             NaN
3     4.961700e+05   182063.00  2.504608e+05  181484.296875             NaN
4     7.272043e+05   340009.75  6.064422e+05  344918.437500             NaN
...            ...         ...           ...            ...             ...
7387  5.069350e+05  1019040.00  4.234370e+05  337381.750000             NaN
7388  6.538187e+05   152753.75  4.611882e+05  457434.625000             NaN
7389  1.040879e+06   294082.00  4.388998e+05  569235.750000             NaN
7390  1.001755e+06   722656.00  1.959685e+06  760903.312500             NaN
7391  5.703433e+04    14655.25  3.587609e+04   20476.740234             NaN

[7392 rows x 5 columns]

# Old Data: 

In [ ]:
# GET PARAMETERS
from os import listdir
import os
import sys
import pandas as pd 
# Get Parent folder : 
current_path = os.getcwd()
parent_dir = os.path.abspath(os.path.join(current_path, '..'))
if parent_dir not in sys.path:
    sys.path.insert(0, parent_dir)

from build_inputs.tile_ids_around_stations import buffer_between_tile_ids_and_subway_station,netmob_data_FOLDER_PATH,PATH_iris,DATA_FOLDER_PATH
from build_inputs.NetMob_pattern_around_stations import tackle_all_days

epsilon = 100
(gdf_stations,joined,result,maxi_nb_tile) = buffer_between_tile_ids_and_subway_station(epsilon,netmob_data_FOLDER_PATH,PATH_iris)

In [ ]:
transfer_mode = 'DL'

apps = ['Google_Maps','Uber','Facebook','Instagram','WhatsApp','Deezer']
for app in apps: 
    print('App: ',app)
    folder_days = [day for day in listdir(f'{netmob_data_FOLDER_PATH}/{app}') if (not day.startswith('.')) ] 
    dic_time_series = tackle_all_days(result,netmob_data_FOLDER_PATH,folder_days,app,dic_time_series={},assert_transfer_mode=transfer_mode)
    for station_i in dic_time_series.keys():
        dic_time_series[station_i] = dic_time_series[station_i].sort_index()
    break

In [ ]:
from plotting.TS_analysis import plot_subway_patterns,drag_selection_box
from preprocess_subway_15 import get_trigram_correspondance
from bokeh.palettes import Turbo256 as palette
from bokeh.plotting import show,output_notebook,save,output_file
from bokeh.layouts import column

df_correspondance = get_trigram_correspondance()

Metro_A_stations = ['Ampère Victor Hugo', 'Bellecour', 'Charpennes',
       'Cordeliers', 'Cusset','Flachet', 'Foch','Gratte Ciel', 'Hôtel de ville - Louis Pradel',
       'La soie', 'Laurent Bonnevay','Masséna', 'Perrache', 'République Villeurbanne']
Metro_A_TRG = list(df_correspondance.set_index('Station').loc[Metro_A_stations].values.reshape(-1))


In [ ]:

df_NetMob_consumption = pd.DataFrame({station: dic_time_series[station].mean(axis=1).sort_index() for station in Metro_A_TRG})
df_NetMob_consumption = df_NetMob_consumption.rename(columns = {Metro_A_TRG[k]:Metro_A_stations[k] for k in range(len(Metro_A_stations))})

width=1500
height=400
p1 = plot_subway_patterns(dataset.df,Metro_A_stations,palette,width,height,title=f'Trafic Volume by stations')
p2 = plot_subway_patterns(df_NetMob_consumption,Metro_A_stations,palette,width,height,title = f'Google-Maps Volume around stations ({epsilon}m)')
select = drag_selection_box(dataset.df,p1,p2,width=width,height=height//3)
output_notebook()
grid = column(p1,p2,select)
show(grid)

output_notebook()

if False: 
    output_file(filename=f"Google_Maps_consumption_{epsilon}m_around_stations.html")
    save(grid)
#show(p)

# Other : 

In [8]:
from plotting.TS_analysis import plot_subway_patterns,drag_selection_box
from preprocess_subway_15 import get_trigram_correspondance
from bokeh.palettes import Turbo256 as palette
from bokeh.plotting import show,output_notebook,save,output_file
from bokeh.layouts import column

df_correspondance = get_trigram_correspondance()

Metro_A_stations = ['Ampère Victor Hugo', 'Bellecour', 'Charpennes',
       'Cordeliers', 'Cusset','Flachet', 'Foch','Gratte Ciel', 'Hôtel de ville - Louis Pradel',
       'La soie', 'Laurent Bonnevay','Masséna', 'Perrache', 'République Villeurbanne']
Metro_A_TRG = list(df_correspondance.set_index('Station').loc[Metro_A_stations].values.reshape(-1))
df_NetMob_consumption = pd.DataFrame({station: dic_time_series[station].mean(axis=1).sort_index() for station in Metro_A_TRG})
df_NetMob_consumption = df_NetMob_consumption.rename(columns = {Metro_A_TRG[k]:Metro_A_stations[k] for k in range(len(Metro_A_stations))})
width=1500
height=400
p1 = plot_subway_patterns(dataset.df,Metro_A_stations,palette,width,height,title=f'Trafic Volume by stations')
p2 = plot_subway_patterns(df_NetMob_consumption,Metro_A_stations,palette,width,height,title = f'Google-Maps Volume around stations ({epsilon}m)')
select = drag_selection_box(dataset.df,p1,p2,width=width,height=height//3)
output_notebook()
grid = column(p1,p2,select)
show(grid)

output_notebook()

if False: 
    output_file(filename=f"Google_Maps_consumption_{epsilon}m_around_stations.html")
    save(grid)
#show(p)

Loading BokehJS ...

Loading BokehJS ...

NameError: name 'p' is not defined

In [ ]:



# Get index corresponding to Morning : 
mask = df_dates['hour'].isin([7]) & (df_dates['weekday'].isin([0,1,2,3,4])) 
index_mask = df_dates.index[mask]
masked_morning_Netmob = torch.index_select(netmob_T,0,torch.tensor(index_mask).long())


# Get index corresponding to Evening : 
mask = df_dates['hour'].isin([18,19]) & (df_dates['weekday'].isin([0,1,2,3,4])) 
index_mask = df_dates.index[mask]
masked_evening_Netmob = torch.index_select(netmob_T,0,torch.tensor(index_mask).long())

# masked monday 7:30:
monday_date = coverage_local[30+96*3]
mask = df_dates['dates'].isin([monday_date])
index_mask = df_dates.index[mask]
masked_monday_7_30_NetMob =  torch.index_select(netmob_T,0,torch.tensor(index_mask).long())

In [ ]:
total_recorded_volume = netmob_T.sum(0)
morning_volume = masked_morning_Netmob.sum(0)
evening_volume = masked_evening_Netmob.sum(0)

gdf['total_recorded_volume'] = total_recorded_volume.numpy()


gdf['Morning Volume (Arbitrary Units)'] = (gdf['Morning Volume (Arbitrary Units)']/1e5).round().astype(int)
gdf['evening_volume'] = evening_volume.numpy()

# gdf.explore('total_recorded_volume')
# gdf.explore('morning_volume')



In [57]:
gdf

CODE_IRIS  INSEE_COM                 NOM_COM  IRIS              NOM_IRIS  \
0   692560702      69256          Vaulx-en-Velin   702           Dumas-Genas   
1   692040103      69204       Saint-Genis-Laval   103       Basses Barolles   
2   692020402      69202     Sainte-Foy-lès-Lyon   402  La Gravière Beaunant   
3   692900202      69290            Saint-Priest   202            Marendiers   
4   691990101      69199              Saint-Fons   101     Zone Industrielle   
..        ...        ...                     ...   ...                   ...   
95  690340303      69034        Caluire-et-Cuire   303            Montchoisi   
96  690290102      69029                    Bron   102   Gendarmerie-Garenne   
97  693870802      69387  Lyon 7e Arrondissement   802          Tony Garnier   
98  690340104      69034        Caluire-et-Cuire   104    Coste-Croix-Rousse   
99  692661602      69266            Villeurbanne  1602              Bonnevay   

   TYP_IRIS         x          y  \
0         H  4.927895  45.752268   
1         H  4.787730  45.675048   
2         H  4.777241  45.728988   
3         H  4.956797  45.701878   
4         A  4.845974  45.702589   
..      ...       ...        ...   
95        H  4.856461  45.813190   
96        H  4.911145  45.746146   
97        H  4.825768  45.725706   
98        H  4.832627  45.784875   
99        H  4.907211  45.767397   

                                            NEIGHBORS  \
0             692661602,692560701,692750109,690290102   
1                                 692040202,692040102   
2                       691490201,691490101,692020103   
3   692900201,692900401,692900601,692900701,692900702   
4   691990402,691520104,693870802,692590103,693880701   
..                                                ...   
95  690880102,690340104,690630000,690340502,690340602   
96  692661602,690290301,690290101,690290103,692750...   
97  691490402,691520104,693870601,693870705,693820...   
98  693810402,693890403,691940102,693860104,690340...   
99  692660801,692661502,692560501,690290102,690290...   

                                              STATION  \
0                                               12003   
1                                                None   
2                                                None   
3                                                None   
4                                                None   
..                                                ...   
95                                               None   
96                                               None   
97  7012 7013 7046 7015 7049 7020 7057 7026 7005 7006   
98  4042 9041 9042 4023 9046 4024 4025 4002 4003 4...   
99    10016 10114 10115 10116 10118 10088 10014 10015   

                                             CONTAINS      area  best_score  \
0                                           692560702  1.525888    2.488023   
1                                           692040103  1.467854    5.686247   
2                                           692020402  0.560147    3.175503   
3                                           692900202  1.371523    2.428109   
4                                           691990101  3.407314    2.518320   
..                                                ...       ...         ...   
95            690340303,690340201,690340301,690340302  2.724746    2.743178   
96  690290102,690290205,690290203,690290202,690290...  1.795077    2.632487   
97  693870802,693870801,693870703,693870704,693870901  4.276077    2.370612   
98  690340104,690340103,690340101,690340102,693890...  6.817688    3.776984   
99  692661602,692661704,692661703,692661801,692661...  3.243300    2.404127   

    best_neigh                                           geometry  \
0    692560701  POLYGON ((849528.300 6518224.900, 849392.200 6...   
1    692040102  POLYGON ((839287.700 6508882.800, 839277.200 6...   
2    691490201  POLYGON ((837785.800 6515882.600, 837868.900 6...   
3    692900601 

In [18]:
os.listdir(f'{FOLDER_PATH}/lyon_iris_agg100')

['lyon.shp',
 'lyon.shx',
 'lyon.dbf',
 'lyon.cpg',
 'lyon.prj',
 'zone2stations.csv']